In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

from jupyterthemes import jtplot
jtplot.style()

import os
import cv2
import colorsys
import numpy as np
import pandas as pd

from math import factorial
from plotly import tools
import plotly.plotly as py
import plotly.graph_objs as go
from matplotlib import pyplot as plt

from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import normalize
from sklearn.linear_model import Ridge
from sklearn.preprocessing import PolynomialFeatures
from sklearn.pipeline import make_pipeline

In [2]:
def create_unique_color_float(tag, hue_step=0.41):
    h, v = (tag * hue_step) % 1, 1. - (int(tag * hue_step) % 4) / 5.
    r, g, b = colorsys.hsv_to_rgb(h, 1., v)
    r, g, b = int(255*r), int(255*g), int(255*b)
    return 'rgb('+str(b)+', '+str(g)+', '+str(r)+')'

def regular_plot(df, subplot, scale_color, fig=None, row=1, col=1):
    trace_1 = go.Scatter3d(
        x = df['xmin'],
        y = df['ymin'],
        z = df.index,
        mode = 'markers',
        marker = dict(
            size = 5,
            color =  df.index if scale_color else 'rgb(160, 160, 160)',
            colorscale = 'Viridis', 
            opacity = 0.6
        )
    )
    layout = go.Layout(
        title='Visulization of Detected Pedestrian in Video Frames',
        height=1000,
        width=1930,
        margin=dict(l=0, r=0, b=0, t=0),
        paper_bgcolor='rgba(0,0,0,0)',
        plot_bgcolor='rgba(0,0,0,0)'
    )    
    if(not subplot): return go.Figure(data=[trace_1], layout=layout)
    else: 
        fig.append_trace(trace_1, row, col)
        return fig

def tracks_plot(df, subplot, unique_color, fig=None, row=1, col=1):
    data = []
    From, To = min(df['track_id']), max(df['track_id'])+1
    for track_id in range(From, To):
        df_track = df.loc[df['track_id']==track_id].copy()
        trace = go.Scatter3d(
            x = df_track['xmin'],
            y = df_track['ymin'],
            z = df_track.index,
            mode='markers',
            marker = dict(
                size = 4,
                color = create_unique_color_float(track_id) if unique_color else None,
                opacity = 0.4
            )
#             mode = 'lines',name = 'lines',
#             line = dict(
#                 color = create_unique_color_float(track_id) if unique_color else None,
#                 width = 4
#             )
        )
        data.append(trace)
        if(subplot):
            fig.append_trace(trace, row, col)
            
    layout = go.Layout(
        title='Visulization of Tracked Pedestrian in Video Frames',
        height=1000,
        width=1930,
        margin=dict(l=0, r=0, b=0, t=0),
        paper_bgcolor='rgba(0,0,0,0)',
        plot_bgcolor='rgba(0,0,0,0)'

    )
    if(not subplot): return go.Figure(data=data, layout=layout)
    else: return fig
    
def savitzky_golay(y, window_size, order, deriv=0, rate=1):
    window_size = np.abs(np.int(window_size))
    order = np.abs(np.int(order))
    
    if window_size % 2 != 1 or window_size < 1:
        raise TypeError("window_size size must be a positive odd number")
    if window_size < order + 2: # order should be less than or equal window-2
        raise TypeError("window_size is too small for the polynomials order")
        
    order_range = range(order+1)
    half_window = (window_size -1) // 2
    
    # precompute coefficients
    b = np.mat([[k**i for i in order_range] for k in range(-half_window, half_window+1)])
    m = np.linalg.pinv(b).A[deriv] * rate**deriv * factorial(deriv)
    
    # pad the signal at the extremes with values taken from the signal itself
    firstvals = y[0] - np.abs( y[1:half_window+1][::-1] - y[0] )
    lastvals = y[-1] + np.abs(y[-half_window-1:-1][::-1] - y[-1])
    y = np.concatenate((firstvals, y, lastvals))
    
    return np.convolve( m[::-1], y, mode='valid')

def golay_filter(df_track, window_size=45, order=5):
    if(len(df_track) <= window_size):
        return df_track
    df_track['xmin'] = savitzky_golay(df_track['xmin'].values, window_size=window_size, order=order, deriv=0, rate=1)
    df_track['ymin'] = savitzky_golay(df_track['ymin'].values, window_size=window_size, order=order, deriv=0, rate=1)
    return df_track
    
def poly_interpolate(df_track):
    model = make_pipeline(PolynomialFeatures(5), Ridge(solver='svd'))
    X = np.array(df_track.index).reshape(-1, 1)
    df_track['xmin'] = model.fit(X, df_track['xmin']).predict(X)
    df_track['ymin'] = model.fit(X, df_track['ymin']).predict(X)
    return df_track

def moving_avg(df_track):
    df_track[['xmin','ymin']] = df_track[['xmin','ymin']].rolling(window=10).mean()
    return df_track

def smooth(df, smooth_method):
    polynomials = []
    From, To = min(df['track_id']), max(df['track_id'])+1
    for track_id in range(From, To):
        df_track = df.loc[df['track_id']==track_id].copy()

        if(smooth_method == 'poly'): df_track = poly_interpolate(df_track)
        elif(smooth_method == 'moving'): df_track = moving_avg(df_track)
        elif(smooth_method == 'golay'): df_track = golay_filter(df_track)
            
        polynomials.append(df_track)

    df_smooth = pd.concat(polynomials)
    df_smooth = df_smooth.sort_index()
    return df_smooth

def load_tracks(tracks_file, method, concat = False, is_smooth=False):
    if(concat): tracks_file = tracks_file[:-4] + '_join.csv'    
    df = pd.read_csv(tracks_file, header=None)
    df = df.drop([4,5,6,7,8,9], axis=1)
    df.columns = ['frame_id','track_id','xmin','ymin']
    df.index = df['frame_id']
    df = df.drop(['frame_id'], axis=1)
    
    if(is_smooth):
        df = smooth(df, smooth_method='poly')

    if(method=='minmax'):
        points = MinMaxScaler(feature_range=(0,1)).fit_transform(df[['xmin','ymin']].values)
    elif(method=='normalize'):
        points = normalize(df[['xmin','ymin']].values,norm='l2')
    df['xmin'], df['ymin'] = points[:,0], points[:,1]
    return df

def run(tracks_file, concat=False, vis_track=False, subplot=False, scale_color=False, unique_color=False, is_smooth=False, method='minmax', plotly_file='temp'):
    
    if(not subplot):
        df = load_tracks(tracks_file, method, concat, is_smooth)
        if(vis_track): fig = tracks_plot(df, subplot, unique_color)
        else: fig = regular_plot(df, subplot, scale_color)
    else:
        df = load_tracks(tracks_file, method, concat=False)
        
        fig = tools.make_subplots(rows=3, cols=2,specs=[[{'is_3d': True}, {'is_3d': True}],
                                                        [{'is_3d': True}, {'is_3d': True}],
                                                        [{'is_3d': True}, {'is_3d': True}],
                                                       ], horizontal_spacing = 0.02, vertical_spacing=0.02)
        
        fig = regular_plot(df, subplot, scale_color=False, fig=fig, row=1, col=1)
        fig = regular_plot(df, subplot, scale_color=True, fig=fig, row=1, col=2)
        
        fig = tracks_plot(df, subplot, unique_color, fig, row=2, col=1)
        
        df = load_tracks(tracks_file, method, concat=True)
        fig = tracks_plot(df, subplot, unique_color, fig, row=2, col=2)
        
        df_smooth_1 = smooth(df.copy(),  smooth_method='golay')
        df_smooth_2 = smooth(df.copy(),  smooth_method='poly')
        fig = tracks_plot(df_smooth_1, subplot, unique_color, fig, row=3, col=1)
        fig = tracks_plot(df_smooth_2, subplot, unique_color, fig, row=3, col=2)
        
        fig['layout'].update(height=3200, width=1930, margin=dict(l=0, r=0, b=0, t=0), 
                             title='<br>Visualization of Pedestrian Trajectory',
                             titlefont=dict(size=36)
                            )
        py.image.save_as(fig, filename='trajectory_polt.png')
    return iplot(fig, filename=plotly_file)

# Visualization of Pedestrian Trajectory

In [3]:
# run(tracks_file = '../dataset/tracks/PETS09_1.csv', subplot = True, method = 'minmax', plotly_file='Pedestrain_subplot', unique_color=True)

In [9]:
run(tracks_file = '../dataset/tracks/retail_1.csv', concat=True, vis_track=True, subplot=False, method='minmax', unique_color=True, is_smooth=True, plotly_file='Pedestrian_concat_track')

## Visulization of Detected Pedestrian in Video Frames

In [8]:
run(tracks_file = '../dataset/tracks/PETS09_1.csv', scale_color=False, method = 'minmax', plotly_file='Pedestrian_unlabeled')

In [12]:
run(tracks_file = '../dataset/tracks/PETS09_1.csv', scale_color=True, method = 'minmax', plotly_file='Pedestrian_unlabeled')

In [ ]:
run(tracks_file = '../dataset/tracks/PETS09_7.csv', vis_track = True, method = 'minmax', unique_color=True, plotly_file='Pedestrian_track')

## Concatenated Discrete Points in a Track and Applied Smoothing Method

In [10]:
run(tracks_file = '../dataset/tracks/PETS09_1.csv', concat = True, vis_track = True, subplot = False, method = 'minmax', unique_color=True, is_smooth=True, plotly_file='Pedestrian_concat_track')

In [6]:
run(tracks_file = '../dataset/tracks/PETS09_1.csv', concat = True, vis_track = True, subplot = False, method = 'minmax', unique_color=True, is_smooth=True, plotly_file='Pedestrian_concat_track')